<a href="https://colab.research.google.com/github/cdrowley/notebook-demos/blob/main/rtree_partition_points.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Setup

In [1]:
!pip install folium matplotlib mapclassify rtree --quiet

In [2]:
import geopandas as gpd
import numpy as np

from shapely.geometry import box, Point

from rtree import index

## Generate Fake Points

In [3]:
# bounding box around Denmark
minx, miny = 8.0, 54.5
maxx, maxy = 12.65, 57.75
num_points = 10_000

# generate points
x_coords = np.random.uniform(minx, maxx, num_points)
y_coords = np.random.uniform(miny, maxy, num_points)

# random locations to mimic dense urban areas
city_centers = [(9.0, 55.0), (10.5, 56.0), (11.0, 55.5)]
city_radius = 0.2
city_density = 0.6

num_city_points = int(num_points * city_density)
num_rural_points = num_points - num_city_points

city_x_coords = []
city_y_coords = []
for cx, cy in city_centers:
    city_x_coords.extend(np.random.uniform(cx - city_radius, cx + city_radius, num_city_points // len(city_centers)))
    city_y_coords.extend(np.random.uniform(cy - city_radius, cy + city_radius, num_city_points // len(city_centers)))

x_coords = np.concatenate((x_coords[:num_rural_points], city_x_coords))
y_coords = np.concatenate((y_coords[:num_rural_points], city_y_coords))

# get GeoDataFrame
points = gpd.points_from_xy(x_coords, y_coords)
gdf = gpd.GeoDataFrame(geometry=points, crs="EPSG:4326")

## Create Spatial Index (r-tree)

In [4]:
idx = index.Index()

# insert points into the spatial index
for i, geom in enumerate(gdf.geometry):
    idx.insert(i, geom.bounds, obj=i)

## Assign leaves to points and get leave bounding boxes

In [5]:
leaves = idx.leaves()

leaves_bbox = []
for leaf in leaves:
  leaf_idx = leaf[0]
  leaf_point_idxs = leaf[1]
  leaf_bbox = leaf[2]

  # add leaf index to associated points
  gdf.loc[leaf_point_idxs, 'leaf_idx'] = leaf_idx

  # grab the bounding box of leaf node
  leaves_bbox.append(box(*leaf_bbox))

leaves_bbox = gpd.GeoDataFrame(geometry=leaves_bbox, crs="EPSG:4326").reset_index()

## Visualise partitioned points and leaf bounding box

In [7]:
m = gdf.explore(
    column='leaf_idx'
    , tooltip=False
    , tiles='CartoDB dark_matter'

    , width='65%'
    , height='65%'

    , cmap='tab20b'
    , marker_kwds={'radius': 1, 'fillOpacity': 0.6}
    , catergorical=True
)

leaves_bbox.explore(m=m, color='white', style_kwds={'fill': False, 'weight': 2}, tooltip=False)

m